In [1]:
from keras import regularizers, initializers, optimizers, callbacks
from keras.preprocessing.sequence import pad_sequences
from keras.preprocessing.text import Tokenizer
from keras.utils.np_utils import to_categorical
from keras.layers import *
from keras.models import Sequential
import pandas as pd
import numpy as np

Using TensorFlow backend.


In [2]:
df = pd.read_csv('../../datasets/complete-set.csv')
del df['Unnamed: 0']
df.dropna()

content  label
0      House Dem Aide: We Didn’t Even See Comey’s Let...      1
1      Ever get the feeling your life circles the rou...      0
2      Why the Truth Might Get You Fired October 29, ...      1
3      Videos 15 Civilians Killed In Single US Airstr...      1
4      Print \nAn Iranian woman has been sentenced to...      1
...                                                  ...    ...
33795  For the first time in more than a decade, impo...      0
33796  Says Donald Trump has bankrupted his companies...      0
33797  John McCain and George Bush have "absolutely n...      0
33798  A new poll shows 62 percent support the presid...      1
33799  No one claims the report vindicating New Jerse...      1

[33800 rows x 2 columns]

In [3]:
texts = df['content']
y = pd.get_dummies(df['label'])
y = np.array(y)

In [4]:
MAX_NB_WORDS = 100000 # max number of words for tokenizer
MAX_SEQUENCE_LENGTH = 1000 # max length of each sentences, including padding
VALIDATION_SPLIT = 0.2 # 20% of data for validation (not used in training)
EMBEDDING_DIM = 200 # embedding dimensions for word vectors
GLOVE_DIR = "embeddings/glove.6B."+str(EMBEDDING_DIM)+"d.txt"

In [ ]:
tokenizer = Tokenizer(num_words=MAX_NB_WORDS)
tokenizer.fit_on_texts(texts)
sequences = tokenizer.texts_to_sequences(texts)
word_index = tokenizer.word_index

In [24]:
#print(type(word_index))
print(np.asarray(sequences[7]))
#print('Vocabulary size:', len(word_index))

[ 1448    35  1237  2606    29 19323  1446   429     6  6661  1182     2
  2125     1  3450     4  1135     6     1   241   120    26  2215     1
   429 58728 35317  3771    33  1490    10     1  6155     7    16    45
  5714  6597   916  2236    11 31455  7575 18200     1   176   909   571
   459   119    27  3993    43   673     4    33    27     5   728  2157
    28 35317   784     2    20   554    18     5  2070  3789    12 11428
  2821  1420    82    12    29  1926  4782   145     3     1   238     2
    28  3790   145 21868     1   234  2791    59   486    61   300   280
    14     8   640     2     1   466    11    28 35317    17  3968    23
   613  2629   136   736     1   234    30     5  1224  9393   234    11
    16    17    28 76200   729    13     1 17387   907   279     7   322
    10     1   234   166     5  1206    12     1   673     3    68  8945
  7141    33     6  1331   649     7    16    45    24  1575   310    28
 76200   728  1420     8  2119     2   244  2822  9

In [6]:
data = pad_sequences(sequences, padding = 'post', maxlen = MAX_SEQUENCE_LENGTH)
indices = np.arange(data.shape[0])
np.random.shuffle(indices)
data = data[indices]
labels = y[indices]

In [7]:
num_validation_samples = int(VALIDATION_SPLIT*data.shape[0])
x_train = data[: -num_validation_samples]
y_train = labels[: -num_validation_samples]
x_val = data[-num_validation_samples: ]
y_val = labels[-num_validation_samples: ]

In [ ]:
embeddings_index = {}

f = open(GLOVE_DIR, encoding='utf8')
print('Loading Glove from:', GLOVE_DIR,'…', end='')
for line in f:
    values = line.split()
    word = values[0]
    embeddings_index[word] = np.asarray(values[1:], dtype='float32')

f.close()
print("Done.\n Proceeding with Embedding Matrix…", end="")

In [10]:
embedding_matrix = np.random.random((len(word_index) + 1, EMBEDDING_DIM))
for word, i in word_index.items():
    #if i == 0:
    embedding_vector = embeddings_index.get(word)
if embedding_vector is not None:
    embedding_matrix[i] = embedding_vector
#print("Completed!")

the
to
of
and
a
in
that
is
for
on
”
with
was
it
as
he
said
by
are
have
at
be
his
not
from
this
has
mr
an
but
they
i
who
you
—
had
or
trump
their
about
we
will
more
one
would
were
been
she
her
people
all
which
what
if
new
when
out
so
its
there
up
can
like
no
after
also
than
president
our
other
some
clinton
them
into
over
just
do
time
state
now
us
him
could
many
even
years
because
states
how
only
most
two
your
first
american
government
my
those
last
united
year
any
it’s
these
against
world
news
where
before
did
being
hillary
then
get
while
s
obama
may
campaign
election
u
“the
going
ms
make
way
house
me
made
know
very
back
much
white
think
country
“i
media
day
say
during
political
should
don’t
percent
2016
through
here
see
war
trump’s
since
down
national
still
told
donald
well
public
000
according
take
such
work
–
want
right
police
law
under
another
times
own
1
between
former
off
including
go
million
called
says
russia
around
same
long
both
never
party
york
officials
part
good
federal
rep

replace
core
shut
estimated
corrupt
familiar
interesting
tough
abedin
ii
elect
professional
concluded
obvious
suggest
promises
sen
eye
pennsylvania
normal
train
minority
heavy
guns
pentagon
figures
widely
coup
apartment
supply
allegations
therefore
empire
parliament
offers
youtube
writer
selling
zone
arrest
mention
approved
repeal
seriously
runs
joint
male
collapse
blame
size
smith
healthy
agent
territory
discussed
condition
appeal
owned
silver
potentially
institutions
wing
finance
vehicle
delivered
determined
wins
infrastructure
finding
users
developed
michigan
guilty
controlled
argument
surveillance
style
colleagues
chemical
quality
river
jones
year’s
advisers
extremely
aircraft
raising
executives
messages
claiming
increasing
guys
married
destroy
grand
christians
nice
nearby
jail
otherwise
broken
investigations
instance
70
village
guard
apple
qaeda
meaning
scheduled
advantage
refugee
indian
wisconsin
resolution
“my
chris
cabinet
asia
people’s
gender
changing
francisco
established
con

purchase
lord
admit
roles
singer
columnist
schumer
moreover
addressed
outrage
atmosphere
gained
losses
successfully
surprising
dan
dc
sharp
department’s
editorial
fort
forcing
corps
ronald
universities
photographs
disclosure
warrant
socialist
soccer
43
waste
mary
à
suffer
formal
sport
shootings
roof
cheap
oval
mountain
heading
drove
vowed
witnesses
establish
technical
units
regulators
deeper
injury
columbia
penalty
champion
commissioner
minnesota
ap
heritage
rescue
located
constantly
drama
tony
meat
kingdom
silent
districts
expanded
deficit
resulted
hacked
celebrity
65
headlines
mandate
doors
accurate
profile
adopted
dispute
feelings
milk
undocumented
aim
subscribe
revelations
ha
statistics
ross
nominees
brian
42
guardian
calif
investments
reveals
surely
stepped
vitamin
removal
function
weekly
writers
cops
master
succeed
tired
advertisement
basketball
castro
surgery
spiritual
kremlin
arrests
prospect
solutions
handling
exact
tonight
fate
funny
xi
universal
deployed
actress
studio
perfo

subway
alaska
korea’s
sits
considers
authoritarian
designated
59
depend
abuses
man’s
displaced
comfort
stark
operatives
сша
hussein
swimming
“even
colleges
chase
flew
stressed
structures
participating
neutral
feminist
luck
instructions
element
bell
hotels
they’d
irish
transcript
fiction
convictions
assess
maine
portrayed
bubble
factories
más
checked
meaningful
yellow
suggestion
cnn’s
violate
larry
devos
veritas
consultant
channels
delivery
dramatically
doesn't
christopher
edition
reviews
strongest
committing
practical
submit
slaves
passes
fee
kurds
expenses
samsung
gore
“every
franklin
contribution
arabs
tips
bolton
attributed
presumably
sand
lengthy
cyber
pam
cop
he's
lebanon
instances
christianity
urge
literature
bundy
loyalty
jill
auto
wilson
formerly
sleeping
presents
wider
acid
apology
shoulder
celebrating
covers
bizarre
releases
fails
tap
marco
heaven
fleet
parking
addresses
manipulation
inform
attackers
nervous
mall
holes
permits
permitted
espn
dump
households
contractors
censor

assertion
reopening
practically
processed
costly
sich
insight
retain
coastal
victories
breathing
accomplish
wolf
caller
shit
reversed
landslide
souls
launching
trauma
“his
famously
baghdad
meantime
outraged
cares
boats
filling
obesity
tragic
beloved
uprising
memoir
subtle
anxious
tribune
ahmad
duties
nunes
spends
legend
meets
douglas
patriotic
unarmed
“more
factions
charitable
reservation
territories
suburbs
makeup
68
terry
nicht
max
detective
freeze
accounting
explosives
fishing
“like
carson
mitchell
mentally
120
revenge
benefited
persecution
torn
implemented
milwaukee
governors
raids
admin
shell
couples
chairwoman
hoax
advances
hamilton
sexist
seekers
maduro
staged
utility
naked
seventh
seal
syndrome
alarming
husband’s
slogan
valid
qualify
motivation
economically
communism
financially
stunned
periods
converted
plate
fantasy
mother’s
suspension
cotton
detectives
trending
keith
instructed
illicit
dennis
reactions
frequency
processing
woman’s
recover
enacted
favorable
61
jose
media’s
ei

...

qanita
yahya’s
،،
بتفتح
النفس
تذكرنا
بعمليات
عياش
نتنسم
ذكراه
العطرة
قليل
قنيطة
ahmadqanita89
shaweesh
ayash
أبناء
العياش
عادوا
يا
ابناء
وخير
دليل
حسين
الشاويش
hshshaweesh
القدس،
زهرة
المدائن
يتجلى
الإصرار
الغزاة
الانتفاضة
متواصلة،
شراسة
قمع
العدو
وتآمر
الشقيق
قتلى
اصابة
حالات
حرجة
جميعهم
جنود
البطوليةاللهم
أثخن
بني
صهيون
وأرنا
فيهم
عجيب
قدرتك
mhmdyjber
ثأر
البطل؛
تعود
حرة
ramadan32583280
larkspur
mambo
overscheduling
trip’s
multiuse
“backslapping
accessible”
tagine
corby
baldino
kimball’s
willoughby’s
diangelo’s
marbles…
reacted…
vitus
tmrw
“roots’’
family’’
hamm’s
“bloodline”
crackle’s
schumer”
middleditch
“silcon
7azszm3ukj
mrnorvell
yvx5mqaxkv
h⚓️u
ravenhuwolf
nodaktrav
natedh78
theycallme501
tapper”
'aggressive'
kd0jkhqmug
‘soros
“obstruct”
standupforus
المغاربة
يذهلون
ويبتكرون
طريقة
لتجفيف
الملاعب
بإضرام
i5g7
فاجأ
لبطولة
الدار
البيضاء
للتنس
الجميع،
سكبوا
ملاعب
البطولة
وأضرموا
أرضيته
لتجفيفها
بسرعة
مياه
فبعد
الغزيرة
هطلت
الملعب،
قرر
سكب
وإضرام
تجفيفها
بسرعة،
لاستكمال
مباراة
التنس


‘raison
d’être’
barnase
barstar
glufosinate
comparators
098263
96033
tehrangeles
mohebat
touraj
farideh
sahinaz
hdtpjejtc3
vpeotus
“completely”
“weighty
‘brevity
of……
earthrise
tfa
extremist’s
tomahawks
dive”
stifled”
“concentrated
“eds
meds”
rebirths
pendall
conventioneers
kahr
“massively
mantua’s
“drexel
chrestina
narrin
caped
“guitar
christmas2016
meeksfamily
godisgood
jimjordanphotography
jeremymeeks
jimjordan
aniversary
rateme
slaving
mystifyingly
cyberfeminist
cyberfeminism
undersharing
tual
pudner
gymboree
stutler
friese
tests”
“deepstategate”
walkback
collusion”
leginsurrection
obamaworld
“perjury”
“partisan”
chambless
trepidations
“mormons
corroon
lizama
majors’s
“tragedy”
justice4khalid
marjayoun
“khalid’s
“wanton
tical
tory’s
spendings
psychiatry’s
overmedication
stucker
cooperriis
nikkel
nonpsychiatric
“patient”
medicalized
hornstein
ziedonis
reykjanes
hitaveita
sudurnesja
landsvirkjun
orkuveita
reykjavíkur
rig—actually
“thor”
landward
‘dragon
p4wmmrvk61
renewablesnews
bore

unops
¡confirmado
¿montesinismo
postores
¡quieren
tumbarse
¡españoles
alianzas
¿conspira
¿marcianos
venusinos
¡aún
rebanar
cuestionario
mininter
cayó
¡liquidando
¿eso
¡en
trompo
¿reina
¿empresas
francesas
tae6fnykgjc
org—which
activity—from
‘point’
‘outta’
game—life
football—the
“argued”
“reopen
refrigerator”
“crocuses
unerringly
mengering’s
reichler
bingguo
“lackey
“laughingstock
“revise
stance”
‘smiling’
asbill
burck
capozzolo
mcdonnells’
particularized
”thought
teamsheaporter
nhpolitics
jeanieforrester
repseanduffy
‘refugee’
neigborhood
“neigbours
barati’s
cavalli’s
harlem”
“blackness”
castings
chukwudi
nattered
overmanagement
“smerps
rdr
pluspoint
angular2
scaffolded
cto’s
initech
1363
travertine
alessio
cristofaro
aventine
tanneries
coraria
septimiana
septimius
rushed”
mcclatchey
§§
3106
wkow
defalco
russianoff
straphangers
‘multicultural
utopia’
“gina
cotsana’s
“centrally
alleged”
stuart’s
radiofreepalestine
hazard’s
chacour
sunglassed
‘potted’
ostrander’s
70ad
135ad
‘liberated’


085
“scampaign”
“therapeutic
podestaemails27
wikileaksphase3
satanichillary
wikileaks28
rwaopo8fas
aussies
deplorabledan2
hvbiefavit
5cw8nw6azs
jr4trump
‘therapeutic
answered”
avoide
peoople
klingon
neoconed
primitivism
wihout
siona
narváez
putrefied
gnaws
disperses
susbys
syndros
gamesunday
backfields
championshipsunday
pats’
“pedestrian”
ben”
maurkice
“father’s
“fathers
cuanalo
chenhan
stards
£816
szjhkgfxcpe
netcast
tattle
“parallel”
“conspiratorial”
msb
‘acceptance’
‘tolerance’
conspiratorial”
norell
‘tug
zaslow
stovroff
bz2jaz2w88
'gun'…no
msh2cpccle
kurier
assaults”
prosectors
“dangers”
overlay”
sheli
“xitler
“dzud
local”
“cutthroat”
‘presidential
tricks’
gecko
redistributes
rif
harasta
“casting
wmtw
joe6mvh02s
mecollegedem
heiden
“brushed
“entrench”
homebrewed
‘trusted
kampung
melayu
“ahok”
awi
setyono
otso
militants”
cookers”
ichwanul
nurul
sukri
“questioning
“agus
anshorut
daulah
“auction”
“doggystyle”
“shoot”
17’s
tannehill’s
seedings
carr’s
gennette
cap”
relocation”
‘private

orthodontia
isone
anwr
u201cthirty
u201d
zanesville
hesecured
kotek
legionnaires
controversyabout
wherepresident
necap
belgiums
duggars
roading
britishand
govjaynixon
moleg
greenest
commonwealths
brookhavens
rugsthey
pilaf
cryptosporidium
ch2m
chafin
votingto
madigans
hewas
federalbudget
surveille
candidateterri
numberonein
energyresources
isnumber
obamacars
2070
alabamians
baraboo
kitzhabers
immigrantspay
robaina
saysthere
americanscant
obey's
slouches
withnutritional
mannatech
detert
tva
oxendine
trucker's
soonerthan
feingolds
fred's
gianna
jessen's
undertaxed
obamasown
andwas
stilltooracist
allencast
votefor
2003bushtax
congressadjourned
tuggey
toimplement
gunviolence
radel
gallaghers
uaw
mica's
precleared
anglers
gsu
1one
raffled
sotomayor's
australias
vawa
cuccinellis
julin
mikal
villanovas
predominantislamist
michigans
obamashealth
lpez
'tax
potshoot
forcommunist
poors
jindals
gainrevenue
bradleys
latvala
offlexible
factorand
bybilloreilly
saysruben
connecticuts
amajority
support

In [27]:
print(embedding_matrix.shape)

(240109, 200)


In [11]:
model = Sequential()
#model.add(Input(shape=(MAX_SEQUENCE_LENGTH)))
model.add(Embedding(len(word_index) + 1, EMBEDDING_DIM, weights = [embedding_matrix], input_length = MAX_SEQUENCE_LENGTH, trainable=False, name = 'embeddings'))
model.add(LSTM(60, return_sequences=True,name='lstm_layer'))
model.add(GlobalMaxPool1D())
model.add(Dropout(0.1))
model.add(Dense(50, activation="relu"))
model.add(Dropout(0.1))
model.add(Dense(2, activation="sigmoid"))

In [12]:
model.compile(optimizer='adam', loss='binary_crossentropy', metrics = ['accuracy'])

In [ ]:
history = model.fit(x_train, y_train, epochs = 10, batch_size=128, validation_data=(x_val, y_val))

Train on 27040 samples, validate on 6760 samples
Epoch 1/10
10624/27040 [==========>...................] - ETA: 19:46 - loss: 0.6871 - accuracy: 0.5355